# Práctica 2. Extracción de entidades

Se comienza importando los módulos que se emplearán en esta práctica:

In [1]:
import nltk, re, pprint

Los archivos `.txt` se leerán directamente desde la URL por lo que se importa el siguiente módulo:

In [2]:
from urllib import request

Los textos con los que se trabajarán serán Orgullo y Prejuicio de Jane Austen (en su versión original) y Azul... de Rubén Darío también en su versión original.

In [3]:
url_azul = 'https://www.gutenberg.org/files/52894/52894-0.txt'
url_orgullo  = 'https://www.gutenberg.org/files/1342/1342-0.txt'

Se procede a continuación a su lectura y carga (esta celda tarda un tiempo porque procede a descargar ambos libros):

In [4]:
response_azul = request.urlopen(url_azul)
response_orgullo = request.urlopen(url_orgullo)
raw_azul = response_azul.read().decode('utf8')
raw_orgullo = response_orgullo.read().decode('utf8')
type(raw_azul)
type(raw_orgullo)

str

Comprobamos que la carga se ha realizado correctamente visualizando el principio de ambos libros y contando el número de palabras:

In [5]:
print("Azul... tiene",len(raw_azul), "palabras y Orgullo y Prejuicio tiene",len(raw_orgullo))

Azul... tiene 217573 palabras y Orgullo y Prejuicio tiene 717618


In [6]:
print(raw_azul[:103])

﻿The Project Gutenberg EBook of Azul..., by Rubén Darío

This eBook is for the use of anyone anywhere


In [7]:
print(raw_orgullo[:100])

﻿The Project Gutenberg EBook of Pride and Prejudice, by Jane Austen

This eBook is for the use of 


Una vez cargados los libros se procede al preprocesamiento.

## Preprocesamiento

En primer lugar se detectan los idiomas de los textos. Para ello es necesario importar un nuevo módulo:

In [8]:
import textacy
diccionario = {'es':'español', 'en':'inglés'}
print("Azul... está escrito en", diccionario[textacy.text_utils.detect_language(raw_azul)],"mientras que Orgullo y Prejuicio está en", diccionario[textacy.text_utils.detect_language(raw_orgullo)] )

Azul... está escrito en español mientras que Orgullo y Prejuicio está en inglés


A continuación se procede a separar las frases. Para ello se cargan los respectivos tokenizadores y se ejecutan sobre los textos:

In [13]:
nltk.download('punkt')
sentence_tokenizer = nltk.data.load('tokenizers/punkt/english.pickle')
frases_tokenizer = nltk.data.load('tokenizers/punkt/spanish.pickle')

In [11]:
frases = frases_tokenizer.tokenize(raw_azul)
frases[10:15]

['¿Por qué, en este caso, lo azul (aunque en francés\r\nno sea _bleu_, sino _azur_, que es más poético) ha de ser cifra, símbolo\r\ny superior predicamento que abarque lo ideal, lo etéreo, lo infinito,\r\nla serenidad del cielo sin nubes, la luz difusa, la amplitud vaga y sin\r\nlímites, donde nacen, viven, brillan y se mueven los astros?',
 'Pero aunque\r\ntodo esto y más surja del fondo de nuestro ser y aparezca a los ojos del\r\nespíritu, evocado por la palabra _azul_, ¿qué novedad hay en decir que\r\nel arte es todo esto?',
 'Lo mismo es decir que el arte es imitación de la\r\nNaturaleza, como lo definió Aristóteles: la percepción de todo lo\r\nexistente y de todo lo posible, y su reaparición o representación por el\r\nhombre en signos, letras, sonidos, colores o líneas.',
 'En suma: yo, por\r\nmás vueltas que le doy, no veo en eso de que _el arte es lo azul_ sino\r\nuna frase enfática y vacía.',
 'Sea, no obstante, el arte _azul_, o del color que se quiera.']

In [12]:
sentences = sentence_tokenizer.tokenize(raw_orgullo)
sentences[10:15]

['What a fine thing for our girls!”\r\n\r\n“How so?',
 'How can it affect them?”\r\n\r\n“My dear Mr. Bennet,” replied his wife, “how can you be so tiresome!',
 'You\r\nmust know that I am thinking of his marrying one of them.”\r\n\r\n“Is that his design in settling here?”\r\n\r\n“Design!',
 'Nonsense, how can you talk so!',
 'But it is very likely that he\r\n_may_ fall in love with one of them, and therefore you must visit him as\r\nsoon as he comes.”\r\n\r\n“I see no occasion for that.']

Tras esto se procede a la separación en palabras, en este caso se requiere un único tokenizador:

In [14]:
palabras = nltk.word_tokenize(raw_azul)
palabras[220:250]

['comencé',
 'a',
 'leerlo',
 '.',
 'Confieso',
 'que',
 'al',
 'principio',
 ',',
 'a',
 'pesar',
 'de',
 'la',
 'amable',
 'dedicatoria',
 'con',
 'que',
 'usted',
 'me',
 'envía',
 'un',
 'ejemplar',
 ',',
 'miré',
 'el',
 'libro',
 'con',
 'indiferencia',
 '...',
 'casi']

In [15]:
words = nltk.word_tokenize(raw_orgullo)
words[220:250]

['Park',
 'is',
 'let',
 'at',
 'last',
 '?',
 '”',
 'Mr.',
 'Bennet',
 'replied',
 'that',
 'he',
 'had',
 'not',
 '.',
 '“',
 'But',
 'it',
 'is',
 ',',
 '”',
 'returned',
 'she',
 ';',
 '“',
 'for',
 'Mrs.',
 'Long',
 'has',
 'just']

Por último se procede a calcular las formas normales de cada palabra tanto en español como en inglés. Para Azul:

In [37]:
from nltk.stem import WordNetLemmatizer
wordnet_lemmatizer = WordNetLemmatizer()
nltk.download('wordnet')
palabras_normalizadas = list(range(0,len(raw_azul)))
contador1 = 0
for palabra in palabras:
    palabras_normalizadas[contador1] = wordnet_lemmatizer.lemmatize(palabra, pos = 'v')
    contador1=contador1+1

[nltk_data] Downloading package wordnet to
[nltk_data]     /Users/arturosanchezpalacio/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


In [38]:
palabras_normalizadas[400:700]

['más',
 'surja',
 'del',
 'fondo',
 'de',
 'nuestro',
 'ser',
 'y',
 'aparezca',
 'a',
 'los',
 'ojos',
 'del',
 'espíritu',
 ',',
 'evocado',
 'por',
 'la',
 'palabra',
 '_azul_',
 ',',
 '¿qué',
 'novedad',
 'hay',
 'en',
 'decir',
 'que',
 'el',
 'arte',
 'es',
 'todo',
 'esto',
 '?',
 'Lo',
 'mismo',
 'es',
 'decir',
 'que',
 'el',
 'arte',
 'es',
 'imitación',
 'de',
 'la',
 'Naturaleza',
 ',',
 'como',
 'lo',
 'definió',
 'Aristóteles',
 ':',
 'la',
 'percepción',
 'de',
 'todo',
 'lo',
 'existente',
 'y',
 'de',
 'todo',
 'lo',
 'posible',
 ',',
 'y',
 'su',
 'reaparición',
 'o',
 'representación',
 'por',
 'el',
 'hombre',
 'en',
 'signos',
 ',',
 'letras',
 ',',
 'sonidos',
 ',',
 'color',
 'o',
 'líneas',
 '.',
 'En',
 'suma',
 ':',
 'yo',
 ',',
 'por',
 'más',
 'vueltas',
 'que',
 'le',
 'doy',
 ',',
 'no',
 'veo',
 'en',
 'eso',
 'de',
 'que',
 '_el',
 'arte',
 'es',
 'lo',
 'azul_',
 'sino',
 'una',
 'frase',
 'enfática',
 'y',
 'vacía',
 '.',
 'Sea',
 ',',
 'no',
 'obstan

y para Orgullo y Prejuicio:

In [39]:
normalized_words = list(range(0, len(raw_orgullo)))
contador2 = 0
for word in words:
    normalized_words[contador2]= wordnet_lemmatizer.lemmatize(word, pos="v")
    contador2=contador2+1

In [40]:
normalized_words[200:500]

['My',
 'dear',
 'Mr.',
 'Bennet',
 ',',
 '”',
 'say',
 'his',
 'lady',
 'to',
 'him',
 'one',
 'day',
 ',',
 '“',
 'have',
 'you',
 'hear',
 'that',
 'Netherfield',
 'Park',
 'be',
 'let',
 'at',
 'last',
 '?',
 '”',
 'Mr.',
 'Bennet',
 'reply',
 'that',
 'he',
 'have',
 'not',
 '.',
 '“',
 'But',
 'it',
 'be',
 ',',
 '”',
 'return',
 'she',
 ';',
 '“',
 'for',
 'Mrs.',
 'Long',
 'have',
 'just',
 'be',
 'here',
 ',',
 'and',
 'she',
 'tell',
 'me',
 'all',
 'about',
 'it.',
 '”',
 'Mr.',
 'Bennet',
 'make',
 'no',
 'answer',
 '.',
 '“',
 'Do',
 'you',
 'not',
 'want',
 'to',
 'know',
 'who',
 'have',
 'take',
 'it',
 '?',
 '”',
 'cry',
 'his',
 'wife',
 'impatiently',
 '.',
 '“',
 '_You_',
 'want',
 'to',
 'tell',
 'me',
 ',',
 'and',
 'I',
 'have',
 'no',
 'objection',
 'to',
 'hear',
 'it.',
 '”',
 'This',
 'be',
 'invitation',
 'enough',
 '.',
 '“',
 'Why',
 ',',
 'my',
 'dear',
 ',',
 'you',
 'must',
 'know',
 ',',
 'Mrs.',
 'Long',
 'say',
 'that',
 'Netherfield',
 'be',
 'take'

En esta parte se comienzan a apreciar diferencias entre el proceso con los dos idiomas el inglés no es perfecto transformar por ejemplo 'has' o 'was' en 'ha' y 'wa' pero en general es bastante bueno. Elimina algunos plurales como servants o fortunes y mantiene 's importantes como que distingue Mr. y Mrs.

Por el contrario en español los resultados son bastante menos halagüeños. La mayoría de los sustantivos conservan por ejemplo su plural (solo en el fragmento mostrado más de 20 como letras, sonidos, colores, signos, líneas...) y sin embargo otras s's como la de 'es' son eliminadas.

## Análisis Morfológico

A continuación se procede a realizar el análisis morfológico sobre las palabras separadas (sin su forma normal):

Los resultados para inglés son de bastante calidad:

In [22]:
nltk.download('averaged_perceptron_tagger')
tagged_words = nltk.pos_tag(words)
tagged_words[1300:1500]

[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /Users/arturosanchezpalacio/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!


[('.', '.'),
 ('She', 'PRP'),
 ('has', 'VBZ'),
 ('two', 'CD'),
 ('nieces', 'NNS'),
 ('of', 'IN'),
 ('her', 'PRP$'),
 ('own', 'JJ'),
 ('.', '.'),
 ('She', 'PRP'),
 ('is', 'VBZ'),
 ('a', 'DT'),
 ('selfish', 'JJ'),
 (',', ','),
 ('hypocritical', 'JJ'),
 ('woman', 'NN'),
 (',', ','),
 ('and', 'CC'),
 ('I', 'PRP'),
 ('have', 'VBP'),
 ('no', 'DT'),
 ('opinion', 'NN'),
 ('of', 'IN'),
 ('her.', 'NN'),
 ('”', 'NNP'),
 ('“', 'VBZ'),
 ('No', 'RB'),
 ('more', 'RBR'),
 ('have', 'VBP'),
 ('I', 'PRP'),
 (',', ','),
 ('”', 'NNP'),
 ('said', 'VBD'),
 ('Mr.', 'NNP'),
 ('Bennet', 'NNP'),
 (';', ':'),
 ('“', 'NNP'),
 ('and', 'CC'),
 ('I', 'PRP'),
 ('am', 'VBP'),
 ('glad', 'JJ'),
 ('to', 'TO'),
 ('find', 'VB'),
 ('that', 'IN'),
 ('you', 'PRP'),
 ('do', 'VBP'),
 ('not', 'RB'),
 ('depend', 'VB'),
 ('on', 'IN'),
 ('her', 'PRP'),
 ('serving', 'VBG'),
 ('you.', 'NN'),
 ('”', 'NNP'),
 ('Mrs.', 'NNP'),
 ('Bennet', 'NNP'),
 ('deigned', 'VBD'),
 ('not', 'RB'),
 ('to', 'TO'),
 ('make', 'VB'),
 ('any', 'DT'),
 ('repl

Los resultados para español son un auténtico desastre aunque acierta algunos nombres propios:

In [23]:
palabras_analizadas = nltk.pos_tag(palabras)
palabras_analizadas[1300:1500]

[('detrás', 'JJ'),
 ('del', 'FW'),
 ('cual', 'JJ'),
 ('se', 'NN'),
 ('descubre', 'NN'),
 ('la', 'NN'),
 ('condición', 'NN'),
 ('española', 'NN'),
 ('.', '.'),
 ('Ninguno', 'NNP'),
 ('de', 'IN'),
 ('los', 'FW'),
 ('hombres', 'NNS'),
 ('de', 'FW'),
 ('letras', 'FW'),
 ('de', 'FW'),
 ('la', 'FW'),
 ('Península', 'NNP'),
 (',', ','),
 ('que', 'NN'),
 ('he', 'PRP'),
 ('conocido', 'VBZ'),
 ('yo', 'RB'),
 (',', ','),
 ('con', 'NN'),
 ('más', 'NN'),
 ('espíritu', 'NN'),
 ('cosmopolita', 'NN'),
 (',', ','),
 ('y', 'NN'),
 ('que', 'NN'),
 ('más', 'NN'),
 ('largo', 'NN'),
 ('tiempo', 'NN'),
 ('han', 'NN'),
 ('residido', 'NN'),
 ('en', 'IN'),
 ('Francia', 'NNP'),
 ('y', 'NN'),
 ('que', 'NN'),
 ('han', 'NN'),
 ('hablado', 'NN'),
 ('mejor', 'NN'),
 ('el', 'NN'),
 ('francés', 'NN'),
 ('y', 'NN'),
 ('otras', 'FW'),
 ('lenguas', 'NN'),
 ('extranjeras', 'NN'),
 (',', ','),
 ('me', 'PRP'),
 ('ha', 'VBP'),
 ('parecido', 'JJ'),
 ('nunca', 'JJ'),
 ('tan', 'NN'),
 ('compenetrado', 'NN'),
 ('del', 'FW'),
 ('e

## Extracción de entidades

Se procede a continuación a extraer entidades de ambos libros. Para ello analizamos morfológicamente las frases y luego les pasamos el extractor:

In [26]:
nltk.download('maxent_ne_chunker')
nltk.download('words')
sentences_token = [nltk.word_tokenize(sentence) for sentence in sentences]
sentences_tagged = [nltk.pos_tag(sentence) for sentence in sentences_token]
for sentence in sentences_tagged:
    print(nltk.ne_chunk(sentence))

[nltk_data] Downloading package maxent_ne_chunker to
[nltk_data]     /Users/arturosanchezpalacio/nltk_data...
[nltk_data]   Package maxent_ne_chunker is already up-to-date!
[nltk_data] Downloading package words to
[nltk_data]     /Users/arturosanchezpalacio/nltk_data...
[nltk_data]   Unzipping corpora/words.zip.


(S
  ﻿The/NN
  (PERSON Project/NNP Gutenberg/NNP)
  EBook/NNP
  of/IN
  (GPE Pride/NNP)
  and/CC
  Prejudice/NNP
  ,/,
  by/IN
  (PERSON Jane/NNP Austen/NNP)
  This/DT
  eBook/NN
  is/VBZ
  for/IN
  the/DT
  use/NN
  of/IN
  anyone/NN
  anywhere/RB
  at/IN
  no/DT
  cost/NN
  and/CC
  with/IN
  almost/RB
  no/DT
  restrictions/NNS
  whatsoever/RB
  ./.)
(S
  You/PRP
  may/MD
  copy/VB
  it/PRP
  ,/,
  give/VB
  it/PRP
  away/RB
  or/CC
  re-use/VB
  it/PRP
  under/IN
  the/DT
  terms/NNS
  of/IN
  the/DT
  (ORGANIZATION Project/NNP Gutenberg/NNP License/NNP)
  included/VBD
  with/IN
  this/DT
  eBook/NN
  or/CC
  online/NN
  at/IN
  www.gutenberg.org/JJ
  Title/NN
  :/:
  Pride/NN
  and/CC
  Prejudice/NNP
  Author/NNP
  :/:
  (PERSON Jane/NNP Austen/NNP)
  Posting/VBG
  Date/NNP
  :/:
  August/NNP
  26/CD
  ,/,
  2008/CD
  [/NNP
  EBook/NNP
  #/#
  1342/CD
  ]/NN
  (PERSON Release/NNP Date/NNP)
  :/:
  June/NNP
  ,/,
  1998/CD
  Last/JJ
  Updated/VBN
  :/:
  March/NNP
  10/CD
  ,/,
  2

(S
  I/PRP
  have/VBP
  heard/VBN
  you/PRP
  mention/VBP
  them/PRP
  with/IN
  consideration/NN
  these/DT
  last/JJ
  twenty/NN
  years/NNS
  at/IN
  (ORGANIZATION least./JJ)
  ”/NNP
  “/NNP
  Ah/NNP
  ,/,
  you/PRP
  do/VBP
  not/RB
  know/VB
  what/WP
  I/PRP
  suffer./VBP
  ”/JJ
  “/NN
  But/CC
  I/PRP
  hope/VBP
  you/PRP
  will/MD
  get/VB
  over/IN
  it/PRP
  ,/,
  and/CC
  live/VBP
  to/TO
  see/VB
  many/JJ
  young/JJ
  men/NNS
  of/IN
  four/CD
  thousand/NN
  a/DT
  year/NN
  come/VBN
  into/IN
  the/DT
  neighbourhood./JJ
  ”/NNP
  “/NN
  It/PRP
  will/MD
  be/VB
  no/RB
  use/NN
  to/TO
  us/PRP
  ,/,
  if/IN
  twenty/NNS
  such/JJ
  should/MD
  come/VB
  ,/,
  since/IN
  you/PRP
  will/MD
  not/RB
  visit/VB
  them./NN
  ”/NNP
  “/NNP
  Depend/NNP
  upon/IN
  it/PRP
  ,/,
  my/PRP$
  dear/NN
  ,/,
  that/IN
  when/WRB
  there/EX
  are/VBP
  twenty/JJ
  ,/,
  I/PRP
  will/MD
  visit/VB
  them/PRP
  all./RP
  ”/IN
  (PERSON Mr./NNP Bennet/NNP)
  was/VBD
  so/RB
  odd/JJ
 

(S
  At/IN
  our/PRP$
  time/NN
  of/IN
  life/NN
  it/PRP
  is/VBZ
  not/RB
  so/RB
  pleasant/JJ
  ,/,
  I/PRP
  can/MD
  tell/VB
  you/PRP
  ,/,
  to/TO
  be/VB
  making/VBG
  new/JJ
  acquaintances/NNS
  every/DT
  day/NN
  ;/:
  but/CC
  for/IN
  your/PRP$
  sakes/NNS
  ,/,
  we/PRP
  would/MD
  do/VB
  anything/NN
  ./.)
(S
  (GPE Lydia/NNP)
  ,/,
  my/PRP$
  love/NN
  ,/,
  though/IN
  you/PRP
  _are_/VBP
  the/DT
  youngest/JJS
  ,/,
  I/PRP
  dare/VBP
  say/VB
  (PERSON Mr./NNP Bingley/NNP)
  will/MD
  dance/VB
  with/IN
  you/PRP
  at/IN
  the/DT
  next/JJ
  ball./NN
  ”/NNP
  “/NNP
  Oh/NNP
  !/.
  ”/NN
  said/VBD
  (PERSON Lydia/NNP)
  stoutly/RB
  ,/,
  “/PRP
  I/PRP
  am/VBP
  not/RB
  afraid/JJ
  ;/:
  for/IN
  though/IN
  I/PRP
  _am_/VBP
  the/DT
  youngest/JJS
  ,/,
  I/PRP
  'm/VBP
  the/DT
  tallest./NN
  ”/VBD
  The/DT
  rest/NN
  of/IN
  the/DT
  evening/NN
  was/VBD
  spent/VBN
  in/IN
  conjecturing/VBG
  how/WRB
  soon/RB
  he/PRP
  would/MD
  return/VB
  (PERS

(S
  (PERSON Mr./NNP)
  (PERSON Darcy/NNP)
  danced/VBD
  only/RB
  once/RB
  with/IN
  Mrs./NNP
  Hurst/NNP
  and/CC
  once/RB
  with/IN
  (PERSON Miss/NNP Bingley/NNP)
  ,/,
  declined/VBD
  being/VBG
  introduced/VBN
  to/TO
  any/DT
  other/JJ
  lady/NN
  ,/,
  and/CC
  spent/VBD
  the/DT
  rest/NN
  of/IN
  the/DT
  evening/NN
  in/IN
  walking/VBG
  about/IN
  the/DT
  room/NN
  ,/,
  speaking/VBG
  occasionally/RB
  to/TO
  one/CD
  of/IN
  his/PRP$
  own/JJ
  party/NN
  ./.)
(S His/PRP$ character/NN was/VBD decided/VBN ./.)
(S
  He/PRP
  was/VBD
  the/DT
  proudest/JJS
  ,/,
  most/RBS
  disagreeable/JJ
  man/NN
  in/IN
  the/DT
  world/NN
  ,/,
  and/CC
  everybody/NN
  hoped/VBD
  that/IN
  he/PRP
  would/MD
  never/RB
  come/VB
  there/RB
  again/RB
  ./.)
(S
  Amongst/IN
  the/DT
  most/RBS
  violent/JJ
  against/IN
  him/PRP
  was/VBD
  Mrs./NNP
  Bennet/NNP
  ,/,
  whose/WP$
  dislike/NN
  of/IN
  his/PRP$
  general/JJ
  behaviour/NN
  was/VBD
  sharpened/VBN
  into/IN
  

...

(S
  The/DT
  darling/VBG
  wish/NN
  of/IN
  his/PRP$
  sisters/NNS
  was/VBD
  then/RB
  gratified/VBN
  ;/:
  he/PRP
  bought/VBD
  an/DT
  estate/NN
  in/IN
  a/DT
  neighbouring/JJ
  county/NN
  to/TO
  (GPE Derbyshire/NNP)
  ,/,
  and/CC
  (PERSON Jane/NNP)
  and/CC
  (PERSON Elizabeth/NNP)
  ,/,
  in/IN
  addition/NN
  to/TO
  every/DT
  other/JJ
  source/NN
  of/IN
  happiness/NN
  ,/,
  were/VBD
  within/IN
  thirty/JJ
  miles/NNS
  of/IN
  each/DT
  other/JJ
  ./.)
(S
  (GPE Kitty/NNP)
  ,/,
  to/TO
  her/PRP$
  very/RB
  material/JJ
  advantage/NN
  ,/,
  spent/VBD
  the/DT
  chief/NN
  of/IN
  her/PRP$
  time/NN
  with/IN
  her/PRP$
  two/CD
  elder/NN
  sisters/NNS
  ./.)
(S
  In/IN
  society/NN
  so/RB
  superior/JJ
  to/TO
  what/WP
  she/PRP
  had/VBD
  generally/RB
  known/VBN
  ,/,
  her/PRP$
  improvement/NN
  was/VBD
  great/JJ
  ./.)
(S
  She/PRP
  was/VBD
  not/RB
  of/IN
  so/RB
  ungovernable/JJ
  a/DT
  temper/NN
  as/IN
  (GPE Lydia/NNP)
  ;/:
  and/CC
  ,/,
 

(S
  By/IN
  (PERSON Elizabeth/NNP)
  's/POS
  instructions/NNS
  ,/,
  she/PRP
  began/VBD
  to/TO
  comprehend/VB
  that/IN
  a/DT
  woman/NN
  may/MD
  take/VB
  liberties/NNS
  with/IN
  her/PRP$
  husband/NN
  which/WDT
  a/DT
  brother/NN
  will/MD
  not/RB
  always/RB
  allow/VB
  in/IN
  a/DT
  sister/NN
  more/JJR
  than/IN
  ten/CD
  years/NNS
  younger/JJR
  than/IN
  himself/PRP
  ./.)
(S
  (PERSON Lady/JJ)
  (PERSON Catherine/NNP)
  was/VBD
  extremely/RB
  indignant/JJ
  on/IN
  the/DT
  marriage/NN
  of/IN
  her/PRP$
  nephew/NN
  ;/:
  and/CC
  as/IN
  she/PRP
  gave/VBD
  way/NN
  to/TO
  all/PDT
  the/DT
  genuine/JJ
  frankness/NN
  of/IN
  her/PRP$
  character/NN
  in/IN
  her/PRP$
  reply/NN
  to/TO
  the/DT
  letter/NN
  which/WDT
  announced/VBD
  its/PRP$
  arrangement/NN
  ,/,
  she/PRP
  sent/VBD
  him/PRP
  language/NN
  so/RB
  very/RB
  abusive/JJ
  ,/,
  especially/RB
  of/IN
  (GPE Elizabeth/NNP)
  ,/,
  that/IN
  for/IN
  some/DT
  time/NN
  all/DT
  int

(S
  You/PRP
  can/MD
  easily/RB
  comply/VB
  with/IN
  the/DT
  terms/NNS
  of/IN
  this/DT
  agreement/NN
  by/IN
  keeping/VBG
  this/DT
  work/NN
  in/IN
  the/DT
  same/JJ
  format/NN
  with/IN
  its/PRP$
  attached/JJ
  full/JJ
  Project/NNP
  Gutenberg-tm/NNP
  License/NNP
  when/WRB
  you/PRP
  share/NN
  it/PRP
  without/IN
  charge/NN
  with/IN
  others/NNS
  ./.)
(S 1.D/CD ./.)
(S
  The/DT
  copyright/NN
  laws/NNS
  of/IN
  the/DT
  place/NN
  where/WRB
  you/PRP
  are/VBP
  located/VBN
  also/RB
  govern/VBP
  what/WP
  you/PRP
  can/MD
  do/VB
  with/IN
  this/DT
  work/NN
  ./.)
(S
  (GPE Copyright/NNP)
  laws/NNS
  in/IN
  most/JJS
  countries/NNS
  are/VBP
  in/IN
  a/DT
  constant/JJ
  state/NN
  of/IN
  change/NN
  ./.)
(S
  If/IN
  you/PRP
  are/VBP
  outside/IN
  the/DT
  (GPE United/NNP States/NNPS)
  ,/,
  check/VB
  the/DT
  laws/NNS
  of/IN
  your/PRP$
  country/NN
  in/IN
  addition/NN
  to/TO
  the/DT
  terms/NNS
  of/IN
  this/DT
  agreement/NN
  before/IN

(S
  If/IN
  you/PRP
  wish/VBP
  to/TO
  charge/VB
  a/DT
  fee/NN
  or/CC
  distribute/VB
  a/DT
  Project/NNP
  Gutenberg-tm/NNP
  electronic/JJ
  work/NN
  or/CC
  group/NN
  of/IN
  works/NNS
  on/IN
  different/JJ
  terms/NNS
  than/IN
  are/VBP
  set/VBN
  forth/NN
  in/IN
  this/DT
  agreement/NN
  ,/,
  you/PRP
  must/MD
  obtain/VB
  permission/NN
  in/IN
  writing/VBG
  from/IN
  both/CC
  the/DT
  (ORGANIZATION Project/NNP Gutenberg/NNP)
  Literary/NNP
  Archive/NNP
  Foundation/NNP
  and/CC
  (PERSON Michael/NNP Hart/NNP)
  ,/,
  the/DT
  owner/NN
  of/IN
  the/DT
  (ORGANIZATION Project/NNP)
  Gutenberg-tm/NNP
  trademark/NN
  ./.)
(S
  Contact/VB
  the/DT
  (ORGANIZATION Foundation/NNP)
  as/IN
  set/VBN
  forth/NN
  in/IN
  Section/NNP
  3/CD
  below/IN
  ./.)
(S 1.F/CD ./.)
(S 1.F.1/CD ./.)
(S
  Project/NNP
  Gutenberg/NNP
  volunteers/NNS
  and/CC
  employees/NNS
  expend/VBP
  considerable/JJ
  effort/NN
  to/TO
  identify/VB
  ,/,
  do/VB
  copyright/JJ
  research/N

  ./.)
(S
  Its/PRP$
  501/CD
  (/(
  c/NN
  )/)
  (/(
  3/CD
  )/)
  letter/NN
  is/VBZ
  posted/VBN
  at/IN
  http/NN
  :/:
  //pglaf.org/fundraising/NN
  ./.)
(S
  Contributions/NNS
  to/TO
  the/DT
  (ORGANIZATION Project/NNP Gutenberg/NNP)
  Literary/NNP
  Archive/NNP
  Foundation/NNP
  are/VBP
  tax/NN
  deductible/JJ
  to/TO
  the/DT
  full/JJ
  extent/NN
  permitted/VBN
  by/IN
  (GPE U.S./NNP)
  federal/JJ
  laws/NNS
  and/CC
  your/PRP$
  state/NN
  's/POS
  laws/NNS
  ./.)
(S
  The/DT
  (ORGANIZATION Foundation/NNP)
  's/POS
  principal/JJ
  office/NN
  is/VBZ
  located/VBN
  at/IN
  4557/CD
  (PERSON Melan/NNP)
  Dr./NNP
  S./NNP
  Fairbanks/NNP
  ,/,
  (ORGANIZATION AK/NNP)
  ,/,
  99712./CD
  ,/,
  but/CC
  its/PRP$
  volunteers/NNS
  and/CC
  employees/NNS
  are/VBP
  scattered/VBN
  throughout/IN
  numerous/JJ
  locations/NNS
  ./.)
(S
  Its/PRP$
  business/NN
  office/NN
  is/VBZ
  located/VBN
  at/IN
  809/CD
  North/JJ
  1500/CD
  (GPE West/NNP)
  ,/,
  (PERSON Salt/

Los resultados en inglés son aceptables aunque se cometen varios errores. Detecta nombres propios y localizaciones con bastante precisión (aunque añade algunas palabras posteriores a punto (y por tanto con mayúscula) a nombre propio sin serlo).

In [27]:
frases_tokenizadas = [nltk.word_tokenize(frase) for frase in frases]
frases_etiquetadas = [nltk.pos_tag(frase) for frase in frases_tokenizadas]
for frase in frases_etiquetadas:
    print(nltk.ne_chunk(frase))

(S
  ﻿The/NN
  (PERSON Project/NNP Gutenberg/NNP)
  EBook/NNP
  of/IN
  (GPE Azul/NNP)
  .../:
  ,/,
  by/IN
  (PERSON Rubén/NNP Darío/NNP)
  This/DT
  eBook/NN
  is/VBZ
  for/IN
  the/DT
  use/NN
  of/IN
  anyone/NN
  anywhere/RB
  at/IN
  no/DT
  cost/NN
  and/CC
  with/IN
  almost/RB
  no/DT
  restrictions/NNS
  whatsoever/RB
  ./.)
(S
  You/PRP
  may/MD
  copy/VB
  it/PRP
  ,/,
  give/VB
  it/PRP
  away/RB
  or/CC
  re-use/VB
  it/PRP
  under/IN
  the/DT
  terms/NNS
  of/IN
  the/DT
  (ORGANIZATION Project/NNP Gutenberg/NNP License/NNP)
  included/VBD
  with/IN
  this/DT
  eBook/NN
  or/CC
  online/NN
  at/IN
  www.gutenberg.org/license/JJ
  Title/NN
  :/:
  Azul/NN
  .../:
  (PERSON Obras/NNP Completas/NNP Vol/NNP)
  ./.)
(S
  IV/NNP
  Author/NNP
  :/:
  (PERSON Rubén/NNP Darío/NNP Illustrator/NNP)
  :/:
  (PERSON Enrique/NNP Ochoa/NNP Release/NNP Date/NNP)
  :/:
  August/NNP
  25/CD
  ,/,
  2016/CD
  [/NNP
  EBook/NNP
  #/#
  52894/CD
  ]/JJ
  Language/NN
  :/:
  (PERSON Spanish/

(S
  (GPE Es/NNP)
  más/NN
  :/:
  en/JJ
  los/NN
  perfiles/NNS
  ,/,
  en/FW
  los/FW
  refinamientos/NN
  ,/,
  en/FW
  las/FW
  exquisiteces/NNS
  del/VBP
  pensar/JJ
  y/NN
  del/NN
  sentir/NN
  del/NN
  autor/NN
  hay/NN
  tanto/NN
  de/IN
  francés/NN
  ,/,
  que/JJ
  yo/NN
  forjé/NN
  una/JJ
  historia/NN
  a/DT
  mi/NN
  antojo/NN
  para/NN
  explicármela/NN
  ./.)
(S
  (GPE Supuse/NNP)
  que/NN
  el/NN
  autor/NN
  ,/,
  nacido/JJ
  en/FW
  (PERSON Nicaragua/NNP)
  ,/,
  había/NN
  ido/NN
  a/DT
  París/NNP
  a/DT
  estudiar/JJ
  para/NN
  médico/NN
  o/NN
  para/NN
  ingeniero/NN
  ,/,
  o/JJ
  para/NN
  otra/JJ
  profesión/NN
  ;/:
  que/CC
  en/FW
  (GPE París/NNP)
  había/NN
  vivido/NN
  seis/NN
  o/IN
  siete/JJ
  años/NN
  ,/,
  con/NN
  artistas/NNS
  ,/,
  literatos/NNS
  ,/,
  sabios/NNS
  y/VBP
  mujeres/NNS
  alegres/VBZ
  de/IN
  por/FW
  allá/NN
  ;/:
  y/CC
  que/JJ
  mucho/NN
  de/IN
  lo/FW
  que/JJ
  sabe/NN
  lo/NN
  había/NN
  aprendido/NN
  de/IN
  viva

(S
  (GPE En/NNP)
  los/NN
  cuentos/NN
  y/NN
  en/IN
  las/FW
  poesías/FW
  todo/FW
  está/FW
  cincelado/NN
  ,/,
  burilado/NN
  ,/,
  hecho/JJ
  para/NN
  que/NN
  dure/NN
  ,/,
  con/NN
  primor/NN
  y/NN
  esmero/NN
  ,/,
  como/NN
  pudiera/NN
  haberlo/NN
  hecho/NN
  (PERSON Flaubert/NNP)
  ,/,
  o/JJ
  el/NN
  parnasiano/NN
  más/NN
  atildado/NN
  ./.)
(S
  Y/NNP
  ,/,
  sin/NN
  embargo/NN
  ,/,
  no/DT
  se/NN
  nota/RB
  el/JJ
  esfuerzo/NN
  ,/,
  ni/JJ
  el/FW
  trabajo/FW
  de/FW
  la/FW
  lima/FW
  ,/,
  ni/FW
  la/FW
  fatiga/FW
  del/FW
  rebuscar/NN
  :/:
  todo/NN
  parece/NN
  espontáneo/NN
  y/NN
  fácil/NN
  y/NN
  escrito/NN
  al/JJ
  correr/NN
  de/IN
  la/FW
  pluma/FW
  ,/,
  sin/FW
  mengua/FW
  de/FW
  la/FW
  concisión/FW
  ,/,
  de/FW
  la/FW
  precisión/FW
  y/FW
  de/FW
  la/FW
  extremada/FW
  elegancia/NN
  ./.)
(S
  (GPE Hasta/NNP)
  las/VBZ
  rarezas/VB
  extravagantes/NNS
  y/JJ
  salidas/FW
  de/FW
  tono/FW
  ,/,
  que/FW
  a/DT
  mí/FW
  me/

(S
  (GPE El/NNP)
  abismo/NN
  de/FW
  lo/FW
  incognoscible/JJ
  queda/NN
  así/NN
  descubierto/NN
  y/NN
  abierto/NN
  ,/,
  y/CC
  nos/JJ
  atrae/NN
  y/NN
  nos/JJ
  da/NN
  vértigo/NN
  ,/,
  y/CC
  nos/NNS
  comunica/VBP
  el/NN
  impulso/NN
  ,/,
  a/DT
  veces/NNS
  irresistible/JJ
  ,/,
  de/FW
  arrojarnos/FW
  en/FW
  él/FW
  ./.)
(S
  (GPE La/NNP)
  situación/NN
  ,/,
  no/DT
  obstante/NN
  ,/,
  no/DT
  es/NN
  incómoda/NN
  para/NN
  la/NN
  gente/FW
  sensata/FW
  de/FW
  cierta/FW
  ilustración/FW
  y/FW
  fuste/NN
  ./.)
(S
  Prescinden/NNP
  de/FW
  lo/FW
  transcendente/FW
  y/FW
  de/FW
  lo/FW
  sobrenatural/JJ
  para/NN
  no/DT
  calentarse/NN
  la/NN
  cabeza/NN
  ni/JJ
  perder/NN
  el/NN
  tiempo/NN
  en/IN
  balde/NN
  ./.)
(S
  (GPE Esta/NNP)
  inclinación/NN
  les/VBZ
  quita/JJ
  no/DT
  pocas/NN
  aprensiones/VBZ
  y/RB
  cierto/JJ
  miedo/NN
  ,/,
  aunque/VBZ
  a/DT
  veces/NNS
  les/VBZ
  infunde/JJ
  otro/NN
  miedo/NN
  y/NN
  sobresalto/NN
  fast

(S
  Usted/VBN
  pide/JJ
  siempre/NN
  más/NN
  al/IN
  hada/NN
  ,/,
  y/NN
  .../:
  «/JJ
  El/NNP
  hada/NN
  entonces/NNS
  me/PRP
  llevó/VBP
  hasta/JJ
  el/NN
  velo/NN
  que/NN
  nos/JJ
  cubre/NN
  las/NNS
  ansias/VBP
  infinitas/NNS
  ,/,
  la/FW
  inspiración/FW
  profunda/FW
  y/FW
  el/FW
  alma/FW
  de/FW
  las/FW
  liras/NNS
  ./.)
(S Y/NNP lo/NN rasgó/NN ./.)
(S
  Y/NNP
  allí/NN
  todo/NN
  era/NN
  aurora./NN
  »/NNP
  Pero/NNP
  aun/NN
  así/NN
  ,/,
  no/DT
  se/JJ
  satisface/NN
  el/NN
  poeta/NN
  ,/,
  y/JJ
  pide/NN
  más/NN
  al/IN
  hada/NN
  ./.)
(S
  (PERSON Tiene/NNP)
  usted/VBD
  otra/JJ
  composición/NN
  ,/,
  la/FW
  que/FW
  lleva/FW
  por/FW
  título/NN
  la/FW
  palabra/FW
  griega/FW
  _Anagke_/FW
  ,/,
  donde/FW
  el/FW
  cántico/FW
  de/FW
  amor/FW
  acaba/FW
  en/FW
  un/JJ
  infortunio/NN
  y/NN
  en/IN
  una/JJ
  blasfemia/NN
  ./.)
(S
  (GPE Suprimiendo/NNP)
  la/NN
  blasfemia/NN
  final/JJ
  ,/,
  que/JJ
  es/NN
  burla/NN
  contra/JJ


...

(S
  MEDALLONES/NNP
  I/PRP
  (ORGANIZATION LECONTE/NNP DE/NNP)
  (ORGANIZATION LISLE/NNP De/NNP)
  las/FW
  eternas/FW
  musas/FW
  el/FW
  reino/NN
  soberano/NN
  recorres/NNS
  ,/,
  bajo/NN
  un/JJ
  soplo/NN
  de/IN
  vasta/FW
  inspiración/NN
  ,/,
  como/NN
  un/JJ
  rajah/NN
  soberbio/NN
  que/NN
  en/FW
  su/NN
  elefante/NN
  indiano/NN
  por/NN
  sus/NN
  dominios/NNS
  pasa/VBP
  de/IN
  rudo/FW
  viento/FW
  al/FW
  son/NN
  ./.)
(S
  (GPE Tú/NNP)
  tienes/NNS
  en/FW
  tu/NN
  canto/NN
  como/NN
  ecos/FW
  de/FW
  (GPE Océano/NNP)
  ;/:
  se/JJ
  ve/NN
  en/IN
  tu/NN
  poesía/NN
  la/NN
  selva/NN
  y/NN
  el/NN
  león/NN
  ;/:
  salvaje/CC
  luz/JJ
  irradia/NN
  la/NN
  lira/FW
  que/NN
  en/FW
  tu/NN
  mano/NN
  derrama/NN
  su/NN
  sonora/NN
  ,/,
  robusta/NN
  vibración/NN
  ./.)
(S
  Tú/NNP
  del/FW
  fakir/NN
  conoces/NNS
  secretos/VBP
  y/JJ
  avatares/NNS
  ;/:
  a/DT
  tu/NN
  alma/NN
  dió/NN
  el/NN
  Oriente/NNP
  misterios/NNS
  seculares/NNS
  ,/,
 

  ./.)
(S
  You/PRP
  may/MD
  use/VB
  this/DT
  eBook/NN
  for/IN
  nearly/RB
  any/DT
  purpose/JJ
  such/JJ
  as/IN
  creation/NN
  of/IN
  derivative/JJ
  works/NNS
  ,/,
  reports/NNS
  ,/,
  performances/NNS
  and/CC
  research/NN
  ./.)
(S
  They/PRP
  may/MD
  be/VB
  modified/VBN
  and/CC
  printed/VBN
  and/CC
  given/VBN
  away/RP
  --/:
  you/PRP
  may/MD
  do/VB
  practically/RB
  ANYTHING/VB
  with/IN
  public/JJ
  domain/NN
  (ORGANIZATION eBooks/NNS)
  ./.)
(S
  (GPE Redistribution/NN)
  is/VBZ
  subject/JJ
  to/TO
  the/DT
  trademark/NN
  license/NN
  ,/,
  especially/RB
  commercial/JJ
  redistribution/NN
  ./.)
(S
  ***/JJ
  START/NN
  :/:
  FULL/NNP
  LICENSE/NNP
  ***/VBD
  (ORGANIZATION THE/NNP)
  (ORGANIZATION FULL/NNP)
  PROJECT/NNP
  GUTENBERG/NNP
  LICENSE/NNP
  PLEASE/NNP
  READ/NNP
  THIS/NNP
  BEFORE/NNP
  YOU/NNP
  (ORGANIZATION DISTRIBUTE/NNP)
  OR/NNP
  USE/NNP
  THIS/NNP
  WORK/NNP
  To/TO
  protect/VB
  the/DT
  (ORGANIZATION Project/NNP)
  Gutenberg

(S
  If/IN
  an/DT
  individual/JJ
  Project/NNP
  Gutenberg-tm/NNP
  electronic/JJ
  work/NN
  is/VBZ
  posted/VBN
  with/IN
  the/DT
  permission/NN
  of/IN
  the/DT
  copyright/NN
  holder/NN
  ,/,
  your/PRP$
  use/NN
  and/CC
  distribution/NN
  must/MD
  comply/VB
  with/IN
  both/DT
  paragraphs/NNS
  1.E.1/CD
  through/IN
  1.E.7/CD
  and/CC
  any/DT
  additional/JJ
  terms/NNS
  imposed/VBN
  by/IN
  the/DT
  copyright/NN
  holder/NN
  ./.)
(S
  Additional/JJ
  terms/NNS
  will/MD
  be/VB
  linked/VBN
  to/TO
  the/DT
  (ORGANIZATION Project/NNP)
  Gutenberg-tm/NNP
  License/NNP
  for/IN
  all/DT
  works/NNS
  posted/VBN
  with/IN
  the/DT
  permission/NN
  of/IN
  the/DT
  copyright/NN
  holder/NN
  found/VBD
  at/IN
  the/DT
  beginning/NN
  of/IN
  this/DT
  work/NN
  ./.)
(S 1.E.4/CD ./.)
(S
  Do/NNP
  not/RB
  unlink/VB
  or/CC
  detach/VB
  or/CC
  remove/VB
  the/DT
  full/JJ
  Project/NNP
  Gutenberg-tm/NNP
  License/NNP
  terms/NNS
  from/IN
  this/DT
  work/NN
  ,/,


(S
  YOU/PRP$
  AGREE/VBP
  THAT/IN
  (ORGANIZATION THE/NNP FOUNDATION/NNP)
  ,/,
  (ORGANIZATION THE/NNP)
  (ORGANIZATION TRADEMARK/NNP)
  OWNER/NNP
  ,/,
  (ORGANIZATION AND/NNP)
  ANY/NNP
  DISTRIBUTOR/NNP
  UNDER/NNP
  THIS/NNP
  AGREEMENT/NNP
  WILL/MD
  (ORGANIZATION NOT/NNP)
  BE/NNP
  LIABLE/NNP
  TO/NNP
  YOU/NNP
  FOR/NNP
  ACTUAL/NNP
  ,/,
  (ORGANIZATION DIRECT/NNP)
  ,/,
  (GPE INDIRECT/NNP)
  ,/,
  (ORGANIZATION CONSEQUENTIAL/NNP)
  ,/,
  (ORGANIZATION PUNITIVE/NNP)
  OR/NNP
  (ORGANIZATION INCIDENTAL/NNP)
  DAMAGES/NNP
  EVEN/NNP
  IF/NNP
  YOU/NNP
  GIVE/NNP
  NOTICE/NNP
  OF/IN
  (ORGANIZATION THE/NNP)
  (ORGANIZATION POSSIBILITY/NNP OF/NNP)
  SUCH/NNP
  DAMAGE/NNP
  ./.)
(S 1.F.3/CD ./.)
(S
  (ORGANIZATION LIMITED/NNP)
  (ORGANIZATION RIGHT/NNP OF/NNP)
  REPLACEMENT/NNP
  OR/NNP
  (ORGANIZATION REFUND/NNP)
  -/:
  If/IN
  you/PRP
  discover/VBP
  a/DT
  defect/NN
  in/IN
  this/DT
  electronic/JJ
  work/NN
  within/IN
  90/CD
  days/NNS
  of/IN
  receiving/VBG
  it/PR

(S
  To/TO
  (ORGANIZATION SEND/NNP)
  DONATIONS/NNP
  or/CC
  determine/VB
  the/DT
  status/NN
  of/IN
  compliance/NN
  for/IN
  any/DT
  particular/JJ
  state/NN
  visit/NN
  http/NN
  :/:
  //pglaf.org/NN
  While/IN
  we/PRP
  can/MD
  not/RB
  and/CC
  do/VB
  not/RB
  solicit/VB
  contributions/NNS
  from/IN
  states/NNS
  where/WRB
  we/PRP
  have/VBP
  not/RB
  met/VBN
  the/DT
  solicitation/NN
  requirements/NNS
  ,/,
  we/PRP
  know/VBP
  of/IN
  no/DT
  prohibition/NN
  against/IN
  accepting/VBG
  unsolicited/JJ
  donations/NNS
  from/IN
  donors/NNS
  in/IN
  such/JJ
  states/NNS
  who/WP
  approach/VBP
  us/PRP
  with/IN
  offers/NNS
  to/TO
  donate/VB
  ./.)
(S
  International/NNP
  donations/NNS
  are/VBP
  gratefully/RB
  accepted/VBN
  ,/,
  but/CC
  we/PRP
  can/MD
  not/RB
  make/VB
  any/DT
  statements/NNS
  concerning/VBG
  tax/NN
  treatment/NN
  of/IN
  donations/NNS
  received/VBN
  from/IN
  outside/IN
  the/DT
  (GPE United/NNP States/NNPS)
  ./.)
(S (GPE

En español la extracción de entidades es bastante pobre. Extrae como personas "Obras completas o Spanish Character".  Es una buena primera aproximación pero es mejorable tal y como se muestra a continuación.

## Probando Spacy

Con el objetivo de mejorar el reconocimiento y la extracción de entidades vamos a probar el módulo `Spacy`. Para ello es necesario instalar el módulo así como en este caso sus versiones para inglés y español mediante la terminal. Una vez hecho esto se importa el módulo, se selecciona el idioma y se carga el texto:

In [34]:
import spacy
nlp =spacy.load('en')
adapted_text = nlp(raw_orgullo)

A continuación se presenta una lista de todas las palabras que Spacy ha reconocido como entidad así como su clasificación:

In [35]:
for word in adapted_text.ents:
    print(word.text, word.label_)

Jane Austen

 PERSON
Project ORG
Gutenberg License PERSON
Jane Austen PERSON
August 26, 2008 DATE
1342 MONEY
June, 1998
 DATE
March 10, 2018 DATE
Anonymous Volunteers





 PERSON
Jane Austen



 PERSON
Chapter 1


 LAW
Bennet PERSON
one day DATE
Bennet PERSON
Long PERSON
Bennet PERSON
Long PERSON
Netherfield PERSON
England GPE
Monday DATE
four CARDINAL
Morris PERSON
Michaelmas PERSON
the end of next week DATE
four CARDINAL
five thousand a year DATE
Bennet PERSON
one CARDINAL
one CARDINAL
Bingley PERSON
five CARDINAL
Bingley PERSON
one CARDINAL
William PERSON
Lady Lucas PERSON
Bingley PERSON
Lizzy PERSON
Lizzy PERSON
half CARDINAL
Jane PERSON
Lydia ORG
Lizzy PERSON
Bennet PERSON
these last twenty years DATE
four CARDINAL
twenty CARDINAL
Depend PERSON
twenty CARDINAL
Bennet PERSON
three CARDINAL
twenty years DATE
Bennet PERSON
Bingley PERSON
second ORDINAL
Bingley PERSON
Lizzy PERSON
Bingley PERSON
Elizabeth PERSON
Long PERSON
Long PERSON
two CARDINAL
Bennet PERSON
Bennet PERSON
Kitty P

Phillipses PRODUCT
the next day DATE
Longbourn
 PERSON
the evening TIME
Phillips PERSON
Elizabeth PERSON
Jane PERSON
two CARDINAL
Jane PERSON
Collins PERSON
Bennet PERSON
Phillips PERSON
Lady
Catherine PERSON
Chapter 16


 LAW
Collins PERSON
Bennet PERSON
five CARDINAL
a suitable hour TIME
Meryton GPE
Wickham PERSON
Collins PERSON
summer DATE
Rosings ORG
first ORDINAL
Phillips PERSON
only one CARDINAL
Lady Catherine PERSON
eight hundred pounds QUANTITY
Lady Catherine PERSON
Phillips PERSON
Wickham PERSON
Elizabeth PERSON
Wickham PERSON
Phillips ORG
Wickham PERSON
Elizabeth PERSON
Wickham PERSON
Collins PERSON
Phillips PERSON
Phillips PERSON
Wickham PERSON
Elizabeth PERSON
Lydia PERSON
first ORDINAL
Lydia ORG
Wickham PERSON
Elizabeth PERSON
Darcy PERSON
Wickham PERSON
Netherfield PERSON
Meryton PERSON
Darcy PERSON
About a month DATE
Elizabeth PERSON
Derbyshire PERSON
Wickham PERSON
ten thousand CARDINAL
Elizabeth PERSON
Bennet PERSON
yesterday DATE
Darcy PERSON
Elizabeth PERSON
four day

Maria PERSON
out--

 PERSON
Eliza GPE
Elizabeth PERSON
Maria PERSON
two CARDINAL
Elizabeth PERSON
Lady Catherine PERSON
Maria PERSON
Lady Catherine PERSON
Jenkinson PERSON
de Bourgh PERSON
Charlotte GPE
Charlotte PERSON
de Bourgh PERSON
Elizabeth PERSON
Collins PERSON
Charlotte GPE
William PERSON
Elizabeth PERSON
Miss de Bourgh PERSON
Collins PERSON
two CARDINAL
Rosings ORG
the next day DATE
Chapter 29 LAW
Collins PERSON
Lady
Catherine PERSON
Sunday DATE
the evening TIME
William PERSON
the whole day DATE
next morning TIME
Rosings PERSON
Collins PERSON
Elizabeth--

 PERSON
Lady
Catherine PERSON
Lady Catherine PERSON
two CARDINAL
three CARDINAL
Lady Catherine PERSON
Maria Lucas
 PERSON
Rosings ORG
St. James's ORG
about half CARDINAL
Collins PERSON
Lewis de Bourgh PERSON
Maria PERSON
William PERSON
Elizabeth PERSON
Lady
Catherine PERSON
Collins PERSON
Lady
Catherine PERSON
Jenkinson PERSON
Collins PERSON
St. James's ORG
William PERSON
Elizabeth PERSON
three CARDINAL
Lady Catherine PERSON


Brighton GPE
Phillips PERSON
Kitty PERSON
Elizabeth PERSON
Darcy PERSON
Lydia ORG
Forster PERSON
Brighton GPE
Lydia PERSON
three_ months' DATE
Lydia ORG
Forster PERSON
Bennet PERSON
Kitty GPE
Lydia ORG
Kitty PERSON
Forster PERSON
Lydia ORG
two years DATE
Elizabeth PERSON
Jane PERSON
Elizabeth PERSON
Lydia PERSON
Lydia ORG
Forster PERSON
Brighton GPE
Lydia ORG
Elizabeth PERSON
Lydia ORG
Bennet PERSON
Lizzy PERSON
Lydia ORG
Lydia ORG
sixteen CARDINAL
Kitty PERSON
Lydia ORG
Bennet PERSON
Jane PERSON
three CARDINAL
Longbourn ORG
Lydia ORG
Brighton GPE
Forster PERSON
Brighton GPE
Elizabeth PERSON
Lydia ORG
Brighton GPE
at least six CARDINAL
Lydia ORG
Brighton GPE
Lydia PERSON
Elizabeth PERSON
Wickham PERSON
first ORDINAL
Meryton ORG
Longbourn PERSON
Elizabeth PERSON
Hunsford GPE
Fitzwilliam PERSON
Darcy PERSON
three
weeks DATE
Rosings ORG
Rosings ORG
Nearly three weeks DATE
Darcy PERSON
Wickham PERSON
Elizabeth PERSON
Wickham PERSON
Wickham PERSON
a few minutes TIME
Darcy PERSON
Miss de Bou

Jane PERSON
Wickham PERSON
Elizabeth PERSON
Lydia ORG
three months DATE
Jane PERSON
Elizabeth PERSON
Lydia ORG
day DATE
William Goulding PERSON
Elizabeth PERSON
Lydia ORG
Jane PERSON
Lydia ORG
first ORDINAL
Phillips PERSON
Lucases PERSON
Wickham PERSON
Hill PERSON
two CARDINAL
half CARDINAL
Brighton GPE
Lydia PERSON
Newcastle ORG
one CARDINAL
two CARDINAL
Elizabeth PERSON
ten days DATE
Wickham PERSON
London GPE
Bennet PERSON
Wickham PERSON
Lydia ORG
Elizabeth PERSON
Lydia ORG
Wickham PERSON
the first of September DATE
One morning TIME
two CARDINAL
Elizabeth PERSON
Lizzy PERSON
Elizabeth PERSON
St. Clement's ORG
Wickham PERSON
eleven CARDINAL
Monday DATE
morning TIME
ten CARDINAL
Wickham PERSON
ten CARDINAL
London GPE
the Little Theatre ORG
Stone PERSON
the hour TIME
ten minutes' TIME
Darcy PERSON
Darcy PERSON
Elizabeth PERSON
Wickham PERSON
Wickham PERSON
Jane PERSON
Elizabeth PERSON
Lydia PERSON
Wickham PERSON
Elizabeth PERSON
Darcy PERSON
Lydia ORG
Jane PERSON
Elizabeth PERSON
Lydia 

States GPE
Project Gutenberg PERSON
Project Gutenberg-tm PERSON
Project Gutenberg-tm PERSON
Project Gutenberg PERSON
Project ORG
Project ORG
Gutenberg License PERSON
Project Gutenberg-tm PERSON
the United States GPE
Project Gutenberg PERSON
Project Gutenberg-tm PERSON
Project Gutenberg-tm PERSON
Project Gutenberg-tm
 PERSON
Project Gutenberg-tm PERSON
Project ORG
1.E.6 CARDINAL
Project Gutenberg-tm PERSON
Project Gutenberg-tm PERSON
Project Gutenberg-tm
License PERSON
Project Gutenberg-tm PERSON
Project Gutenberg-tm PERSON
20% PERCENT
Project Gutenberg-tm PERSON
Project ORG
60 days DATE
Project Gutenberg Literary Archive Foundation ORG
Section 4 LAW
Project Gutenberg Literary Archive Foundation ORG
30 days DATE
Project Gutenberg-tm PERSON
License PERSON
Project Gutenberg-tm PERSON
90 days DATE
Project Gutenberg-tm PERSON
Project Gutenberg-tm
 PERSON
Project Gutenberg Literary Archive Foundation ORG
Michael
Hart ORG
Project ORG
Section 3 LAW
Gutenberg PERSON
Project Gutenberg-tm PERSON


En inglés se observan unos resultados incluso mejores que con `stacy` en los que se detectan números (ordinales y cardinales), muchas expresiones relacionadas con el tiempo y las localizaciones. Aun así también comete errores como añadir `Depend` como nombre propio. 

Análogamente para español:

In [36]:
nlp =spacy.load('es')
texto_adaptado = nlp(raw_azul)
for palabra in texto_adaptado.ents:
    print(palabra.text, palabra.label_)

﻿The Project Gutenberg PER
EBook of Azul MISC
Rubén Darío

This eBook MISC
eBook MISC
Rubén Darío

Illustrator MISC
Enrique Ochoa

Release Date PER
August 25 MISC
EBook MISC
Spanish

Character MISC
UTF-8

 MISC
START OF ORG
PROJECT GUTENBERG MISC
EBOOK MISC
Josep Cols Canals PER
Chuck Greif and the Online PER
Distributed Proofreading Team ORG
This
 MISC
The Internet Archive MISC
Canadian Libraries PER
Illustration MISC
RUBÉN DARÍO PER
ILUSTRACIONES MISC
ENRIQUE OCHOA MISC
Volumen IV PER
Administración MISC
Editorial
                             MUNDO LATINO MISC
Illustration: ES PROPIEDAD MISC
Madrid LOC
Octubre MISC
América LOC
El título _Azul MISC
Víctor Hugo PER
c’est l’azur MISC
Para mí MISC
¿Por qué MISC
¿ MISC
Lo mismo MISC
Aristóteles PER
En suma: yo MISC
Como sea
 MISC
Lo que a mí me dió mala espina MISC
Víctor Hugo PER
¿Si será éste MISC
Portugal LOC
Víctor Hugo PER
La manía de
 MISC
En resolución yo sospeché MISC
Víctor Huguito PER
Usted PER
Valparaíso LOC
El libro está impre

Recaredo PER
¿No MISC
China LOC
Suzette
 PER
Chopin PER
¡ MISC
Recaredo! MISC
¡ MISC
¿Acaso MISC
¡ LOC
Habían PER
Ya no la quería MISC
Y a ella MISC
Suzette LOC
Recaredo PER
Estaba engañada MISC
¿Lo diría por la rubia MISC
¿Por la ricachona Gabriela MISC
¿O
 MISC
Luisa PER
¿O MISC
Recaredo PER
¿Quién MISC
Sabes cuánto te adoro MISC
Julieta MISC
Suzette LOC
Ella o yo MISC
Si es cierto
 MISC
¿querrás permitir MISC
Recaredo-- LOC
¿Qué MISC
El busto había desaparecido del pedestal de
negro MISC
Suzette LOC
¡Ha muerto ya para ti la emperatriz
de la China!

 MISC
Illustration: ¡Princesa MISC
ROMANZA EN MISC
PROSA ORG
Príncipe Sol PER
Oriente MISC
Pero MISC
He cantado en mis sonetos MISC
Te he visto MISC
Beatriz PER
¡Princesa MISC
¡ MISC
Desaliento! MISC
Tu PER
Me hablaste del camino de la
Gloria MISC
Me hablaste del vergel Amor MISC
Y me dijiste de la terrible MISC
Y ya presa de
 MISC
Desaliento PER
Hugo PER
Hetzel PER
Entonces fué MISC
¡Estrella MISC
Quería PER
Océano LOC
Dios MISC
Tú MISC


En español los resultados son mucho mejores que con `Stacy` aunque continua siendo mucho peor que en inglés debido al entrenamiento del modelo.